# Explore hashtags of posts with stylistic features

In [1]:
# Load 1M dataset

import os
import pandas as pd

data = pd.read_pickle('/mnt/interns/myoder/data/textposts_captions_1m.pkl')
print(len(data))
print(data.columns)

1000000
Index(['post_tags_string', 'post_id', 'activity_time_epoch', 'tumblelog_id',
       'is_private', 'post_title', 'post_short_url', 'post_slug', 'post_type',
       'post_caption', 'post_format', 'post_note_count', 'post_tags',
       'post_content', 'reblogged_from_post_id', 'reblogged_from_metadata',
       'created_time_epoch', 'updated_time_epoch', 'is_submission', 'mentions',
       'source_title', 'source_url', 'post_classifier', 'blog_classifier',
       'activity_date', 'post_body', 'post_body_no_blognames', 'text_type',
       'style_features', 'community'],
      dtype='object')


In [2]:
# Get style feature names
style_feature_names = set([name for names in data['style_features'].map(lambda x: x.keys()) for name in names])
print(len(style_feature_names))
style_feature_names

1417


{'repeated_９',
 'avg_🏈_per_word',
 'avg_⤵_per_word',
 'avg_pwn_per_word',
 'avg_🛤_per_word',
 'avg_🇲_per_word',
 'repeated_³',
 'avg_⚗_per_word',
 'avg_🍏_per_word',
 'avg_📏_per_word',
 'avg_👏_per_word',
 'repeated_ˑ',
 'avg_💳_per_word',
 'avg_💵_per_word',
 'avg_🤓_per_word',
 'avg_🏄_per_word',
 'avg_🚊_per_word',
 'avg_🗑_per_word',
 'avg_🦈_per_word',
 'avg_💓_per_word',
 'avg_🌐_per_word',
 'avg_♠_per_word',
 'repeated_а',
 'avg_🔌_per_word',
 'avg_👢_per_word',
 'avg___per_word',
 'avg_㊙_per_word',
 'avg_📽_per_word',
 'avg_🎌_per_word',
 'avg_🧪_per_word',
 'avg_💝_per_word',
 'avg_📖_per_word',
 'avg_™_per_word',
 'avg_🤜_per_word',
 'avg_🥼_per_word',
 'avg_‼️_per_word',
 'avg_🤷_per_word',
 'repeated_:',
 'repeated_－',
 'avg_⚒_per_word',
 'avg_~_per_word',
 'avg_🛎_per_word',
 'avg_☑_per_word',
 'avg_🤟_per_word',
 'repeated_›',
 'repeated_/',
 'avg_👜_per_word',
 'avg_👘_per_word',
 'repeated_М',
 'repeated_\u200b',
 'avg_🇩_per_word',
 'avg_🎩_per_word',
 'repeated_。',
 'avg_🦰_per_word',
 'avg_🧢_pe

In [8]:
# Check tags for useful stance-label commentary
selected_cols = ['post_type', 'community', 'post_title', 'post_short_url', 'post_body_no_blognames', 'style_features', 'post_tags']

sample = data.sample(100)
sample[selected_cols]

post_type           community  \
2705239  video     writers_on_tumblr    
509025   text      bts                  
347347   text      south_park           
1457461  photo     writers_on_tumblr    
1012652  photo     steven_universe      
234274   photo     south_park           
1795723  text      voltron              
335926   photo     south_park           
1142337  text      studyblr             
1127167  text      simblr               
373194   text      voltron              
2329606  photo     writers_on_tumblr    
999284   text      bts                  
2311145  text      studyblr             
413673   photo     south_park           
680536   photo     south_park           
1227829  photo     miraculous_ladybug   
140228   text      riverdale            
576243   photo     south_park           
2425189  text      bts                  
2226526  text      bts                  
2317915  text      bts                  
134748   text      writers_on_tumblr    
830620   photo     studyblr             
801434   text      simblr               
1909922  photo     simblr               
1655873  text      steven_universe      
29929    photo     bts                  
192393   photo     svtfoe               
70485    text      voltron              
...       ...          ...              
1859161  photo     writers_on_tumblr    
1960529  photo     simblr               
1996171  photo     studyblr             
1212185  video     simblr               
1041908  text      riverdale            
227484   text      south_park           
277954   text      riverdale            
722176   text      writers_on_tumblr    
479122   photo     svtfoe               
250827   photo     miraculous_ladybug   
188920   photo     studyblr             
876513   photo     south_park           
210212   photo     riverdale            
1141067  text      riverdale            
1193043  text      miraculous_ladybug   
764780   photo     south_park           
789311   text      miraculous_ladybug   
14555    photo     miraculous_ladybug   
453706   text      riverdale            
957704   photo     south_park           
1629789  text      miraculous_ladybug   
680343   photo     miraculous_ladybug   
101856   text      riverdale            
889039   photo     simblr               
329135   text      bts                  
67966    text      south_park           
973719   text      simblr               
473697   text      voltron              
63540    photo     miraculous_ladybug   
1184701  photo     simblr               

                                                                                                                          post_title  \
2705239  NaN                                                                                                                           
509025   NaN                                                                                                                           
347347   NaN                                                                                                                           
1457461  NaN                                                                                                                           
1012652  NaN                                                                                                                           
234274   NaN                                                                                                                           
1795723  NaN                                                                                                                           
335926   NaN                                                                                                                           
1142337  NaN                                                                                                                           
1127167  NaN                                                                                             

# Make 1M balanced dataset

In [2]:
# Load data

import os
import pandas as pd
from tqdm import tqdm_notebook as tqdm

data_dirpath = '/mnt/interns/myoder/textposts_captions/'
communities = os.listdir(data_dirpath)
data = {}

for c in tqdm(communities):
    data[c] = pd.read_pickle(os.path.join(data_dirpath, c, f'{c}.pkl')).sample(int(1e5), random_state=9)

In [5]:
# Add community column

for c in communities:
    data[c]['community'] = [c] * len(data[c])

In [6]:
data_1m = pd.concat(data.values())
print(len(data_1m))
print(data_1m.columns)

1000000
Index(['post_tags_string', 'post_id', 'activity_time_epoch', 'tumblelog_id',
       'is_private', 'post_title', 'post_short_url', 'post_slug', 'post_type',
       'post_caption', 'post_format', 'post_note_count', 'post_tags',
       'post_content', 'reblogged_from_post_id', 'reblogged_from_metadata',
       'created_time_epoch', 'updated_time_epoch', 'is_submission', 'mentions',
       'source_title', 'source_url', 'post_classifier', 'blog_classifier',
       'activity_date', 'post_body', 'post_body_no_blognames', 'text_type',
       'style_features', 'community'],
      dtype='object')


In [7]:
# Save

data_1m.to_pickle('/mnt/interns/myoder/textposts_captions_1m.pkl')

# Get post exemplars and see what features capture style

In [4]:
# Load data

import os
import pandas as pd
from tqdm import tqdm_notebook as tqdm

data_dirpath = '/mnt/interns/myoder/data/textposts_captions/'
communities = os.listdir(data_dirpath)
sample100 = {}

for c in communities:
    sample100[c] = pd.read_pickle(os.path.join(data_dirpath, c, f'{c}.pkl')).sample(100, random_state=9)

In [5]:
# Draw samples
from IPython.display import display

pd.set_option('display.max_colwidth', -1)

for c in sorted(communities):
    print(c)
    display(sample100[c].sample(5, random_state=9).loc[:, ['post_type', 'post_title', 'post_short_url', 'post_body_no_blognames', 'style_features']])

bts


post_type    post_title                  post_short_url  \
2198331  text      NaN           https://tmblr.co/ZkKGtk2hdV5Wo   
615994   photo     NaN           https://tmblr.co/ZFajgh2gT8l-a   
466122   photo     NaN           https://tmblr.co/Zwz7xg2hFNcvO   
1462678  text      iit jee exam  https://tmblr.co/ZoTrkZ2YhtZhU   
616661   photo     NaN           https://tmblr.co/ZT0ZWk2VjXD6-   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   post_body_no_blognames  \
2198331  If you were stranded on a desert island which two bts members would you choose ? rb and put ur   in the tags                                                                                                                                                                                                                                                                                                                                                                                                                       
615994   " jiminrolls : the world is your runway "                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          
466122   what happens when I finally meet bts                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               
1462678  iit jee , iit , iit jee exam app , iitian , iitians ,   iit jee preparation apps , jee prep , iit coaching online , iit notes , jee coaching , iit jee physics , iit jee preparation , iit jee preparation app , iit jee question papers , jee preparation , jee preparation app , iit jee main , iit jee study material , iit jee coaching , jee , iit jee mains , iit jee maths , best study apps , iit jee video lectures , jee main , toppr , bansal classes , best studying app , doubtjee mains , engineering entrace exam   
616661   " gguked : that time when jimin killed us all "                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    

                                                                                                                                                                                                                                                                                                                                                                 style_features  
2198331  {'n_words': 23, 'n_characters': 108, 'avg_?_per_word': 0.043478260869565216

miraculous_ladybug


post_type post_title                  post_short_url  \
212243   text      NaN        https://tmblr.co/ZtwySe2ZptXG6   
905173   text      NaN        https://tmblr.co/Z6qaFr2dO8ZPM   
851478   photo     NaN        https://tmblr.co/Z36pRg2ccX8yt   
1891084  text      NaN        https://tmblr.co/Zy-I-a2WbH7V3   
334317   photo     NaN        https://tmblr.co/Zf1Fbx20ptFvm   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       

riverdale


...

post_type post_title                  post_short_url  \
300392   photo     NaN        https://tmblr.co/ZUE_ad2Y5JTsr   
669034   photo     NaN        https://tmblr.co/ZwxJ5Z2ajsnQg   
1007524  photo     NaN        https://tmblr.co/ZE1rLb2V-ibEy   
812805   photo     NaN        https://tmblr.co/ZvuKSb2ZMJ-tY   
22898    photo     NaN        https://tmblr.co/Zuw02c2h7yFwW   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     post_body_no_blognames  \
300392   Tracklist of Star Butterfly - If You Need Me Release on June 15                                                                                                                                                                                                                                                                                                                                                                                                                                      
669034   " spacenarval : you guys really love eclipsa do n’t you ? "                                                                                                                                                                                                                                                                                                                                                                                                                                          
1007524  So I dunno about you all but when I saw that watermelon Marco scene in Saturday ’s episode , I felt like something was n’t quite right . I sensed a lack of continuity , and that ’s something I ca n’t stand for . So I took it upon myself to make this shitty edit . I ca n’t take full credit for it , I did have a friend on a discord who had taken out the background from that scene , I just got rid of the watermelon and added the mango . But everything is right with the world now .   
812805   star doodle                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          
22898    Sunnia started learning ballet at the age of four   ( ๑ ♡ 3 ♡ ๑ )                                                                                                                                                                                                                                                                                                                                                                                                                                    

                                                                                                                                                                                                                                                                                                                              style_features  
300392   {'n_words': 13, 'n_characters': 63, 'avg_-_per_word': 0.07692307692307693, 'avg_punctuation': 0.07692307692307693, 'avg_capitalized_words': 0.6923076923076923, 'avg_capitalized_letters': 0.14285714285714285, 'char_repeats_per_word': 0.0, 'avg_oov_per_word': 0.23076923076923078}                              

voltron


post_type post_title                  post_short_url  \
2035562  text      NaN        https://tmblr.co/ZVYvCt2WfamIR   
99142    photo     NaN        https://tmblr.co/ZzSBhs2W0H11f   
634442   photo     NaN        https://tmblr.co/ZNTJhX2hZfbTc   
858499   text      NaN        https://tmblr.co/Zb_mqY2eLBQwk   
2698276  text      NaN        https://tmblr.co/Z1sN0i2akoViy   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             post_body_no_blognames  \
2035562  I wanna talk for a minute about Lotura and the idea that Lotor is manipulating Allura and will ultimately betray her . Because I see a lot of people insisting that it ’s going to happen , and yet I have n’t seen ANYONE who seems to be able to give a legitimate REASON for Lotor to betray her and Voltron . Which is probably because as things currently stand , that reason does n’t exist . ( Long Post undercut . Screencap heavy ) Lotor wants power ? He HAS it . He ’s currently the Emperor of the Galra . And just like when he was temporary Emperor in S3 while his father was laid up , he ’s not interested in furthering the goals of Zarkon and Haggar and conquering other planets for power . He has a different vision . And it ’s a vision that Allura and the Paladins are helping him to achieve . Lotor is using his half Altean heritage to manipulate Allura into trusting him because he knows she ’s desperate to reconnect with the people she ’s lost ? Okay , cool . So why ’d he wait until she ALREADY TRUSTED HIM to reveal that he ’s half Altean , instead of using it back when he was their prisoner to convince her to give him a chance ? Episode 3 ; Episode 5 ; These are ALL moments that took place BEFORE ; If anything , Lotor looks almost   melancholy while discussing his mixed race heritage with Allura . Which is n’t much of a surprise because we ’ve already seen that it ’s constantly getting thrown in his face as something he ought to be ashamed of . Lotor resents Allura for obtain

writers_on_tumblr


post_type          post_title                  post_short_url  \
2262549  video     NaN                 https://tmblr.co/Z8op9Z2d7F-P7   
2336502  photo     NaN                 https://tmblr.co/Z3QrfZ2ZZXPgR   
5860748  text      Poisoned Daydreams  https://tmblr.co/ZYdOvX2eKIjZA   
5458340  text      NaN                 https://tmblr.co/ZUq2nc2XEiP8d   
217597   text      NaN                 https://tmblr.co/ZXXdiZ2gvq7d6   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              post_body_no_blognames  \
2262549  Wall of Death - Richard Thompson Let me ride on the wall of death one more timeLet me ride on the wall of death one more timeYou can waste your time on the other ridesBut this is the nearest to being aliveLet me take my chances on the Wall of DeathYou can go with the crazy people in the crooked houseYou can fly away on the rocket or spin in the mouseThe tunnel of love might amuse youAnd Noah ’s Ark might confuse you butLet me take my chances on the Wall of DeathOn the Wall of DeathAll the world is far from meOn the Wall of DeathIt ’s the nearest to being freeWell you ’re going nowhere when you ride on the carouselAnd maybe you ’re strong , but what ’s the use of ringing a bellThe switchback will make you crazyBeware of the bearded ladyOh let me take my chances on the Wall of DeathYou are going nowhere when you ride on the carouselAnd maybe you ’re strong , but what ’s the use of ringing a bellThe switchback will make you crazyBeware of the bearded ladyLet me take my chancesLet me take my chancesLet me take my chances                                                                                                                                                                                                                                                                      
2336502  Twenty one pilots is coming back ? ! ?                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  

In [6]:
# Lift examples to study
selected_cols = ['post_type', 'post_title', 'post_short_url', 'post_body_no_blognames', 'style_features', 'post_tags']

display(sample100['bts'].loc[[466122, 616661], selected_cols])
display(sample100['miraculous_ladybug'].loc[[905173, 1891084, 334317], selected_cols])
display(sample100['riverdale'].loc[[62748, 699490], selected_cols])
display(sample100['simblr'].loc[[2271679, 491245, 1244104], selected_cols])
display(sample100['south_park'].loc[[1002735, 966558, 216312], selected_cols])
display(sample100['steven_universe'].loc[[543034, 784204], selected_cols])
display(sample100['studyblr'].loc[[108907, 2036995], selected_cols])
display(sample100['svtfoe'].loc[[22898, 1007524], selected_cols])
display(sample100['voltron'].loc[[2035562, 99142], selected_cols])

post_type post_title                  post_short_url  \
466122  photo     NaN        https://tmblr.co/Zwz7xg2hFNcvO   
616661  photo     NaN        https://tmblr.co/ZT0ZWk2VjXD6-   

                                 post_body_no_blognames  \
466122  what happens when I finally meet bts              
616661  " gguked : that time when jimin killed us all "   

                                                                                                                                                                                                                                                                                      style_features  \
466122  {'n_words': 7, 'n_characters': 36, 'avg_punctuation': 0.0, 'avg_capitalized_words': 0.14285714285714285, 'avg_capitalized_letters': 0.027777777777777776, 'char_repeats_per_word': 0.0, 'avg_oov_per_word': 0.2857142857142857}                                                                
616661  {'n_words': 11, 'n_characters': 47, 'avg_"_per_word': 0.18181818181818182, 'avg_:_per_word': 0.09090909090909091, 'avg_punctuation': 0.2727272727272727, 'avg_capitalized_words': 0.0, 'avg_capitalized_letters': 0.0, 'char_repeats_per_word': 0.0, 'avg_oov_per_word': 0.5454545454545454}   

                                                                                                           post_tags  
466122  {(folks can you tell I don't wanna do work?),(namjoon),(namjoon meme),(bts),(bts meme),(welcome to wendi's)}  
616661  {(this is a religon),(park jimin)}

post_type post_title                  post_short_url  \
905173   text      NaN        https://tmblr.co/Z6qaFr2dO8ZPM   
1891084  text      NaN        https://tmblr.co/Zy-I-a2WbH7V3   
334317   photo     NaN        https://tmblr.co/Zf1Fbx20ptFvm   

                                                                                                                                     post_body_no_blognames  \
905173   HEARTBREAKER THE O GGGGGGG                                                                                                                           
1891084  Me : Okay I finally have a show where I definitely know who the ship the main character with there ’s no way I can mess this up Luka : exists Me :   
334317   " Aesthetic Meme Tales of Miraculous Ladybug and Chat Noir "                                                                                         

                                                                                                                                                                                                                                                                                   style_features  \
905173   {'n_words': 4, 'n_characters': 26, 'avg_punctuation': 0.0, 'avg_capitalized_words': 1.0, 'avg_capitalized_letters': 0.8846153846153846, 'repeated_G': 2, 'char_repeats_per_word': 0.5, 'avg_oov_per_word': 0.25}                                                                           
1891084  {'n_words': 33, 'n_characters': 146, 'avg_:_per_word': 0.09090909090909091, 'avg_punctuation': 0.09090909090909091, 'avg_capitalized_words': 0.21212121212121213, 'avg_capitalized_letters': 0.04794520547945205, 'char_repeats_per_word': 0.0, 'avg_oov_per_word': 0.21212121212121213}   
334317   {'n_words': 11, 'n_characters': 60, 'avg_"_per_word': 0.18181818181818182, 'avg_punctuation': 0.18181818181818182, 'avg_capitalized_words': 0.6363636363636364, 'avg_capitalized_letters': 0.11666666666666667, 'char_repeats_per_word': 0.0, 'avg_oov_per_word': 0.2727272727272727}      

                                                                                                                                                           post_tags  
905173   {(ml),(ml spoilers),(ml s2),(miraculous ladybug),(miraculous ladybug spoilers),(miracujess liveblogs),(miracujess liveblogs: Miraculous Ladybug!)}           
1891084  {(ml spoilers),(miraculous ladybug),(miraculous ladybug season 2),(ml luka)}                                                                                 
334317   {(THE BLUE HAIR IS BAD OK I KINDA TRIED maybe only a little),(miraculous ladybug),(chat noir),(Marinette Dupain-Cheng),(Adrien Agreste),(aesthetic),(edit)}

post_type post_title                  post_short_url  \
62748   photo     NaN        https://tmblr.co/ZB1iKm2hgdJKM   
699490  text      NaN        https://tmblr.co/Z4N0ru2gZ8Oj0   

                                                                                                                                                                     post_body_no_blognames  \
62748   "   : TONI ! ! "                                                                                                                                                                      
699490  Ok while I ’m not exactly happy that Choni have been fighting a lot recently , they ’ve been more real during all of this than ever , and Toni is finally being given a character .   

                                                                                                                                                                                                                                                                                                                                                             style_features  \
62748   {'n_words': 6, 'n_characters': 16, 'avg_!_per_word': 0.3333333333333333, 'avg_"_per_word': 0.3333333333333333, 'avg_:_per_word': 0.16666666666666666, 'avg_punctuation': 0.8333333333333334, 'avg_capitalized_words': 0.16666666666666666, 'avg_capitalized_letters': 0.25, 'repeated_ ': 1, 'char_repeats_per_word': 0.16666666666666666, 'avg_oov_per_word': 1.0}   
699490  {'n_words': 37, 'n_characters': 179, 'avg_,_per_word': 0.05405405405405406, 'avg_._per_word': 0.02702702702702703, 'avg_punctuation': 0.08108108108108109, 'avg_capitalized_words': 0.10810810810810811, 'avg_capitalized_letters': 0.0223463687150838, 'char_repeats_per_word': 0.0, 'avg_oov_per_word': 0.21621621621621623}                                        

                                                            post_tags  
62748   {(toni topaz),(otp: you are sensational),(riverdale),(queue)}  
699490  {(choni),(riverdale)}

post_type post_title                  post_short_url  \
2271679  photo     NaN        https://tmblr.co/Zjo6nY2bgvE8t   
491245   text      NaN        https://tmblr.co/Z6jPjZ2ZvSZfO   
1244104  photo     NaN        https://tmblr.co/ZsjM1y2YC2m4d   

                                                                                                                                                                                                                                                                                                                                                                                                                                                     post_body_no_blognames  \
2271679  Jada : What … ? Butterscotch , is this why you have n’t been feeling well ? ? ? ? Felix : Aw , he ’s so cute ! Can we keep him , Mom ? Jada : - sighs - Of course we can . Charity : Yes ! Let ’s name him Sprinkles ! Felix : No way ! Plus , you got to name the last kitten . Salim : Your brother is right . It ’s his turn . What ’s the little one ’s name , Felix ? Felix : Let ’s call him Rocky . Jada : Rocky it is then . Welcome home , little Rocky .   
491245   alice is all dressed up for spooky day , she just looks like an old mann omg                                                                                                                                                                                                                                                                                                                                                                                         
1244104  Oh , Isobel .. come on ! WE CAN’T AFFORD THIS !   ٩(//̀Д/́/)۶                                                                                                                                                                                                                                                                                                                                                                                                        

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      style_features  \
2271679  {'n_words': 114, 'n_characters': 450, 'avg_!_per_word': 0.03508771929824561, 'avg_,_per_word': 0.05263157894736842, 'avg_-_per_word': 0.017543859649122806, 'avg_._per_word': 0.06140350877192982, 'avg_:_per_word': 0.07017543859649122, 'avg_?_per_word': 0.06140350877192982, 'avg_punctuation': 0.2982456140350877, 'avg_capitalized_words': 0.24561403508771928, 'avg_capitalized_letters': 0.06222222222222222, 'char_repeats_per_word': 0.0, 'avg_oov_per_word': 0.4649122807017544}   
491245   {'n_words': 17, 'n_characters': 76, 'avg_,_per_word': 0.058823529411764705, 'avg_punctuation': 0.058823529411764705, 'avg_capitalized_words': 0.0, 'avg_capitalized_letters': 0.0, 'char_repeats_per_word': 0.0, 'avg_oov_per_word': 0.29411764705882354}                                                                                                                                                                                                                                     
1244104  {'n_words': 13, 'n_characters': 61, 'avg_!_per_word': 0.15384615384615385, 'avg_(_per_word': 0.07692307692307693, 'avg_)_per_word': 0.07692307692307693, 'avg_,_per_word': 0.07692307692307693, 'avg_._per_word': 0.15384615384615385, 'avg_/_per_word': 0.3076923076923077, 'avg_punctuation': 0.8461538461538461, 'avg_capitalized_words': 0.46153846153846156, 'avg_capitalized_letters': 0.3114754098360656, 'char_repeats_per_word':

post_type                          post_title  \
1002735  photo     NaN                                  
966558   photo     NaN                                  
216312   text      starting the kyle profile pic gang   

                         post_short_url  \
1002735  https://tmblr.co/ZT2D0e2bKO-NZ   
966558   https://tmblr.co/ZjyVOl2fdgLYs   
216312   https://tmblr.co/ZHVH3e2gbLURa   

                                                           post_body_no_blognames  \
1002735  " snoorin : Open ur heart 2 salvation "                                    
966558   it was a good weekend , the nuggets won , and he got a kiss from nichole   
216312   ppl with kyle profile pics please interact                                 

                                                                                                                                                                                                                                                                                                                                                                                                style_features  \
1002735  {'n_words': 9, 'n_characters': 39, 'avg_"_per_word': 0.2222222222222222, 'avg_:_per_word': 0.1111111111111111, 'avg_punctuation': 0.3333333333333333, 'avg_capitalized_words': 0.1111111111111111, 'avg_capitalized_letters': 0.02564102564102564, 'char_repeats_per_word': 0.0, 'avg_ur_per_word': 0.1111111111111111, 'avg_2_per_word': 0.1111111111111111, 'avg_oov_per_word': 0.5555555555555556}   
966558   {'n_words': 17, 'n_characters': 72, 'avg_,_per_word': 0.11764705882352941, 'avg_punctuation': 0.11764705882352941, 'avg_capitalized_words': 0.0, 'avg_capitalized_letters': 0.0, 'char_repeats_per_word': 0.0, 'avg_oov_per_word': 0.23529411764705882}                                                                                                                                                 
216312   {'n_words': 7, 'n_characters': 42, 'avg_punctuation': 0.0, 'avg_capitalized_words': 0.0, 'avg_capitalized_letters': 0.0, 'char_repeats_per_word': 0.0, 'avg_oov_per_word': 0.2857142857142857}                                                                                                                                                                                                          

                                                                                                                                        post_tags  
1002735  {(this is worse than that actual long leg craig bs that went around a while back),(:((((((((),(craig tucker),(kenny mccormick),(reblog)}  
966558   {(south park),(kyle broflovski),(nichole daniels),(sp nichyle),(nichyle)}                                                                 
216312   {(south park),(kyle broflovski),(sp kyle),(i just fuckin love my boy my son)}

post_type post_title                  post_short_url  \
543034  photo     NaN        https://tmblr.co/ZW5gkZ2ePbYZo   
784204  text      NaN        https://tmblr.co/ZDHfbm2dVQxk7   

                                                                                                                         post_body_no_blognames  \
543034  Wanna join us ? Sign up NOW !                                                                                                             
784204  Do nt open this its triggering lol When you go to write your suicide note just in case and the pen does nt fucking work 😂 👏 of course .   

                                                                                                                                                                                                                                                                                                                                                                                                          style_features  \
543034  {'n_words': 8, 'n_characters': 29, 'avg_!_per_word': 0.125, 'avg_?_per_word': 0.125, 'avg_punctuation': 0.25, 'avg_capitalized_words': 0.375, 'avg_capitalized_letters': 0.1724137931034483, 'char_repeats_per_word': 0.0, 'avg_oov_per_word': 0.375}                                                                                                                                                              
784204  {'n_words': 30, 'n_characters': 135, 'avg_._per_word': 0.03333333333333333, 'avg_punctuation': 0.03333333333333333, 'avg_capitalized_words': 0.06666666666666667, 'avg_capitalized_letters': 0.014814814814814815, 'char_repeats_per_word': 0.0, 'avg_😂_per_word': 0.03333333333333333, 'avg_👏_per_word': 0.03333333333333333, 'avg_lol_per_word': 0.03333333333333333, 'avg_oov_per_word': 0.26666666666666666}   

                                                                                                                         post_tags  
543034  {(dankmemes),(gaysex),(gaybulge),(instagaysex),(gayselfie),(gaymadrid),(nonbinary),(gaysforlikes),(hairymen),(cocksucker)}  
784204  {(this is my life rn),(absolute fail all around),(suicide tw)}

post_type post_title                  post_short_url  \
108907   photo     NaN        https://tmblr.co/ZQ8Yle2gkf9NJ   
2036995  text      NaN        https://tmblr.co/ZZpObl2eatZn4   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                post_body_no_blognames  \
108907   Today ’s study set - up ! The week after midterms has been rough , I am extremely behind and have a whole ton of group project due . Not to mention some crazy group project problems . I ’m getting very stressed so I ’ve blocked the day off to stay on campus and get a good chunk of my work done !                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        
2036995  whenever alice is uncomfortable , nervous , or overwhelmed she ’ll often turn her focus onto jasper , not only via actual stare or being near him , but very specifically in terms of vision . she ’ll put focus to his future , for a few reasons . one , out of fear / concern for his well - being . two , out of familiarity / her own comfort . three , because of the ease of the action –– she ’s so well attuned to him , and him being her soulmate , she has the easiest time in comparison to any other person in seeing ahead . visions with him are often clearer than the rest and they correlate with the strongest emotional empathy . as in , she does n’t only see those , she sometimes feels those , the best example being the first time she saw his face in a vision and she felt the most at home she ’d ever been . this is n’t always the case , there are multiple factors that make a vision blurry or clear , and it ’s still up in the air based on decisions being made , but all in all , it ’s easy to look for his future .   

                                                                                                                                                                                                                                                                                                                                                                            style_features  \
108907   {'n_words': 64, 'n_characters': 296, 'avg_!_per_word': 0.03125, 'avg_,_per_word': 0.015625, 'avg_-_per_word': 0.015625, 'avg_._per_word': 0.03125, 'avg_punctuation': 0.09375, 'avg_capitalized_words': 0.09375, 'avg_capitalized_letters': 0.02027027027027027, 'char_repeats_per_word': 0.0, 'avg_oov_per_word': 0.203125}     

post_type post_title                  post_short_url  \
22898    photo     NaN        https://tmblr.co/Zuw02c2h7yFwW   
1007524  photo     NaN        https://tmblr.co/ZE1rLb2V-ibEy   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     post_body_no_blognames  \
22898    Sunnia started learning ballet at the age of four   ( ๑ ♡ 3 ♡ ๑ )                                                                                                                                                                                                                                                                                                                                                                                                                                    
1007524  So I dunno about you all but when I saw that watermelon Marco scene in Saturday ’s episode , I felt like something was n’t quite right . I sensed a lack of continuity , and that ’s something I ca n’t stand for . So I took it upon myself to make this shitty edit . I ca n’t take full credit for it , I did have a friend on a discord who had taken out the background from that scene , I just got rid of the watermelon and added the mango . But everything is right with the world now .   

                                                                                                                                                                                                                                                                                                                           style_features  \
22898    {'n_words': 16, 'n_characters': 65, 'avg_(_per_word': 0.0625, 'avg_)_per_word': 0.0625, 'avg_punctuation': 0.125, 'avg_capitalized_words': 0.0625, 'avg_capitalized_letters': 0.015384615384615385, 'char_repeats_per_word': 0.0, 'avg_oov_per_word': 0.5625}                                                                      
1007524  {'n_words': 105, 'n_characters': 482, 'avg_,_per_word': 0.0380952380952381, 'avg_._per_word': 0.047619047619047616, 'avg_punctuation': 0.08571428571428572, 'avg_capitalized_words': 0.13333333333333333, 'avg_capitalized_letters': 0.029045643153526972, 'char_repeats_per_word': 0.0, 'avg_oov_per_word': 0.1619047619047619}   

                                                                                                                                                                                              post_tags  
22898    {(star vs the forces of evil),(star vs las fuerzas del mal),(star vs evil),(svtfoe),(svtfoe fandom),(svtfoe fanart),(svtfoe sunnia),(sunnia butterfly),(starco),(starco child),(chocorry art)}  
1007524  {(star vs the forces of evil),(marco diaz),(mango),(mango Diaz),(edit),(spoilers),(kinda)}

post_type post_title                  post_short_url  \
2035562  text      NaN        https://tmblr.co/ZVYvCt2WfamIR   
99142    photo     NaN        https://tmblr.co/ZzSBhs2W0H11f   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             post_body_no_blognames  \
2035562  I wanna talk for a minute about Lotura and the idea that Lotor is manipulating Allura and will ultimately betray her . Because I see a lot of people insisting that it ’s going to happen , and yet I have n’t seen ANYONE who seems to be able to give a legitimate REASON for Lotor to betray her and Voltron . Which is probably because as things currently stand , that reason does n’t exist . ( Long Post undercut . Screencap heavy ) Lotor wants power ? He HAS it . He ’s currently the Emperor of the Galra . And just like when he was temporary Emperor in S3 while his father was laid up , he ’s not interested in furthering the goals of Zarkon and Haggar and conquering other planets for power . He has a different vision . And it ’s a vision that Allura and the Paladins are helping him to achieve . Lotor is using his half Altean heritage to manipulate Allura into trusting him because he knows she ’s desperate to reconnect with the people she ’s lost ? Okay , cool . So why ’d he wait until she ALREADY TRUSTED HIM to reveal that he ’s half Altean , instead of using it back when he was their prisoner to convince her to give him a chance ? Episode 3 ; Episode 5 ; These are ALL moments that took place BEFORE ; If anything , Lotor looks almost   melancholy while discussing his mixed race heritage with Allura . Which is n’t much of a surprise because we ’ve already seen that it ’s constantly getting thrown in his face as something he ought to be ashamed of . Lotor resents Allura for obtaining the power on Oriande ? HE ’S THE ONE WHO WANTED HER TO GET THAT POWER IN THE FIRST PLACE . Did it sting when he failed the test ? Of course . But Allura still got the power , just as he kn

# Look into non-English posts

In [1]:
# Load example data

import pandas as pd

test = pd.read_pickle('/mnt/interns/myoder/textposts_captions/bts/bts.pkl')
print(test.columns)
test.shape

Index(['post_tags_string', 'post_id', 'activity_time_epoch', 'tumblelog_id',
       'is_private', 'post_title', 'post_short_url', 'post_slug', 'post_type',
       'post_caption', 'post_format', 'post_note_count', 'post_tags',
       'post_content', 'reblogged_from_post_id', 'reblogged_from_metadata',
       'created_time_epoch', 'updated_time_epoch', 'is_submission', 'mentions',
       'source_title', 'source_url', 'post_classifier', 'blog_classifier',
       'activity_date', 'post_body', 'post_body_no_blognames', 'text_type',
       'style_features'],
      dtype='object')


(280157, 29)

In [7]:
# Browse posts

pd.set_option('display.max_colwidth', -1)
test['post_body_no_blognames'].sample(50)

137155    aurjeon : 🔥 🔥 🔥                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               

# Combine text posts and captions

In [6]:
import pandas as pd
from tqdm import tqdm_notebook as tqdm

collections = [
#     'bts',
#     'miraculous_ladybug',
#     'riverdale',
#     'simblr',
#     'south_park',
#     'svtfoe',
#     'steven_universe',
#     'studyblr',
#     'voltron',
    'writers_on_tumblr',
]

for collection in tqdm(collections):
    
    # Load text posts
    fpath = f'../../data/textposts_captions/{collection}_textposts.pkl'
    posts = pd.read_pickle(fpath)
    posts['text_type'] = ['text post'] * len(posts)
    
    # Load captions
    fpath = f'../../data/textposts_captions/{collection}_captions.pkl'
    captions = pd.read_pickle(fpath)
    captions['text_type'] = ['caption'] * len(captions)
    
    # Save out total
    total = pd.concat([posts, captions])
    total.to_pickle(f'../../data/textposts_captions/{collection}.pkl')
    print(collection)
#     print(total.columns)
    print(total.shape)
    print()

writers_on_tumblr
(199908, 28)



# Find emojis for feature extraction

In [1]:
# Load example data

import pandas as pd

test = pd.read_pickle('/mnt/interns/myoder/textposts_captions/bts/bts.pkl')
print(test.columns)
test.shape

Index(['post_tags_string', 'post_id', 'activity_time_epoch', 'tumblelog_id',
       'is_private', 'post_title', 'post_short_url', 'post_slug', 'post_type',
       'post_caption', 'post_format', 'post_note_count', 'post_tags',
       'post_content', 'reblogged_from_post_id', 'reblogged_from_metadata',
       'created_time_epoch', 'updated_time_epoch', 'is_submission', 'mentions',
       'source_title', 'source_url', 'post_classifier', 'blog_classifier',
       'activity_date', 'post_body', 'post_body_no_blognames', 'text_type',
       'style_features'],
      dtype='object')


(280157, 29)

In [3]:
# Try to find emojis

pd.set_option('display.max_colwidth', -1)
test['post_body_no_blognames'].sample(20)

88026     basically i might have a tumor and may or may not be bawling right now and uhm … yeah : d so please spam your girl with adorable bts pics / gifs bc they always make me smile , ty bless 🙏 🏻 💞 ( or just cute soft youtube videos , basically anything combining bangtan w/ uwu culture ya feel )                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             

In [2]:
emoji_post = test.loc[88026, 'post_body_no_blognames']
emoji_post

'basically i might have a tumor and may or may not be bawling right now and uhm … yeah : d so please spam your girl with adorable bts pics / gifs bc they always make me smile , ty bless 🙏 🏻 💞 ( or just cute soft youtube videos , basically anything combining bangtan w/ uwu culture ya feel )'

In [4]:
from emoji import UNICODE_EMOJI
import regex
from collections import Counter

def extract_emoji(text):
    """ Return a dict with emoji and count """
        
    text_emoji = []
    data = regex.findall(r'\X', text)
    text_flags = regex.findall(u'[\U0001F1E6-\U0001F1FF]', text)
    
    for word in data:
        if any(char in UNICODE_EMOJI for char in word):
            text_emoji.append(word)
            
    counter = Counter(text_emoji + text_flags)
    
    return dict(counter)

In [5]:
extract_emoji(emoji_post)

{'🙏': 1, '💞': 1}

# Blog names list

In [2]:
# Load blog names counts
import os
import pandas as pd

blog_names = []

blog_names_fpath = '../../data/blog_names_counts.tsv'
blog_names_counts = pd.read_csv(blog_names_fpath, sep='\t')

blog_names_counts.shape
blog_names_counts.columns

(24068241, 3)

In [28]:
blog_names_counts = blog_names_counts[(blog_names_counts['tumblr_blog_name'].map(lambda x: len(str(x)) > 5))]

In [29]:
# Sort
blog_names_counts.sort_values('post_count', ascending=False, inplace=True)
blog_names_counts.head()

/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


tumblog_id                  tumblr_blog_name  post_count
13042944   145479302                   sexyboysgallery     9997300
9585889    238292343           golfdigest-yahoopartner     8176654
8962879    274173858  business-insider-uk-yahoopartner     3911364
6171265       140583                            caragh     3431238
5300240    237074938        leparisien-fr-yahoopartner     3347110

In [32]:
# Save out top n posts
for n in [10000, 20000, 50000, 100000]:
    with open(f'../../data/blog_names{n}.txt', 'w') as f:
        for name in sorted(blog_names_counts.iloc[:n]['tumblr_blog_name'].tolist()):
            f.write(f'{name}\n')

In [18]:
# Save out with threshold
for post_threshold in post_thresholds:
    with open(f'../../data/blog_names{post_threshold}.txt', 'w') as f:
        for name in sorted(filtered_blog_names[selected_post_threshold]['tumblr_blog_name'].tolist()):
            f.write(f'{name}\n')

In [16]:
post_thresholds = [1000, 10000, 20000, 50000, 100000]
filtered_blog_names = {}

for post_threshold in post_thresholds:
    filtered_blog_names[post_threshold] = blog_names_counts[(blog_names_counts['tumblr_blog_name'].map(lambda x: len(str(x)) > 5)) & (blog_names_counts['post_count']>post_threshold)]
    print(f'{post_threshold}: {len(filtered_blog_names[post_threshold])}')

1000: 3712256
10000: 393590
20000: 137479
50000: 17524
100000: 2313


In [8]:
filtered_blog_names.head()

tumblog_id tumblr_blog_name  post_count
692   445017150           10h-05        1671
705   140238386           2-3-15        1649
710   309139098           290asd        1085
712   400395092           2hated        1778
716    27799285           30cmlp        1318

In [9]:
# Load blog names
import os
from tqdm import tqdm_notebook as tqdm

blog_names = []

blog_names_dirpath = '../../data/blog_names/'

for fname in tqdm(os.listdir(blog_names_dirpath)):
    fpath = os.path.join(blog_names_dirpath, fname)
    with open(fpath) as f:
        blog_names.extend(f.read().splitlines())
        
len(blog_names)

129321132

In [10]:
blog_names = sorted(set(blog_names))
len(blog_names)

129321131

In [12]:
# Save out
with open('../../data/blog_names.txt', 'w') as f:
    for name in blog_names:
        f.write(f'{name}\n')

In [14]:
import random

random.sample(blog_names, 50)

['throwawaytumb7',
 'unlikelydonkeyzipperwombat',
 'luciedrouin',
 'asudak',
 'therealslimjamie',
 'parra25blr',
 'haynmyles',
 'kiloveki',
 'tehehdhdjsnd',
 'lovedelicaterunawaybouquet',
 'rielincireechildblabefro',
 'asktheitalianempire',
 'hypnoducktacobear',
 'tulio-augustowhatzzul',
 'one-directions-super-girl',
 'yesthatbigirl',
 'aniyah-palmucci30',
 'iluvlucyr87',
 'firstangeldeputybakery',
 'fullscissorseggsdonkey',
 'agbgalzzz',
 'sketch-leaves',
 'qualitypersonpandaturkey',
 'a-chocolateira',
 'thehornsoftaurus',
 'teenagebakerybearkid',
 'optimisticspyplaidrascal',
 'luckyauthorhairdowinner',
 'amarillicarlotta',
 'sksk-70',
 'wyoshennanigansandmalarkey',
 'autiemillermdcig-blog',
 'hi-im-ever',
 'arlosposts',
 'green-sky-love',
 'fuzzypainterrebelhound',
 'cvnt-bby',
 'jovialprunesuitcaseplaid',
 'mspapayaa',
 'shamelessangeltacocloud',
 'abdusomatbezzubikov1996',
 'sexykentuckygirl',
 'sillywinnercolorpanda',
 'cookiefriend',
 'juicydroppoppop',
 'trustsyourself',
 'csyrd

# Check caption data

In [1]:
# Load data

import pandas as pd

data = pd.read_csv('../../data/part-v002-o000-r-00000', sep='\t')
print(data.shape)
data.columns

(66918, 25)


/anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3049: DtypeWarning: Columns (2,5) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


Index(['post_tags_string', 'post_id', 'activity_time_epoch', 'tumblelog_id',
       'is_private', 'post_title', 'post_short_url', 'post_slug', 'post_type',
       'post_caption', 'post_format', 'post_note_count', 'post_tags',
       'post_content', 'reblogged_from_post_id', 'reblogged_from_metadata',
       'created_time_epoch', 'updated_time_epoch', 'is_submission', 'mentions',
       'source_title', 'source_url', 'post_classifier', 'blog_classifier',
       'activity_date'],
      dtype='object')

# Check South Park data

In [6]:
pd.set_option('display.max_colwidth', -1)

In [8]:
# Load data

data = pd.read_pickle('../../data/south_park_posts.pkl')

data.sample(30)['post_tags_string']

113677    {(h),(south park),(craig tucker),(txt post)}                                                                                                                                                                                                                                                                        
134322    {(molly shitposts),(sp spoilers),(sp s22),(south park),(stan marsh),(my porno stan icon will help us all)}                                                                                                                                                                                                          
113879    {(creek),(south park),(Danny Says Shit)}                                                                                                                                                                                                                                                                            
61894     {(ooc),(south park),(danganronpa 

# Check BTS data

In [19]:
data.shape

(575920, 27)

In [21]:
pd.set_option('display.max_colwidth', -1)

In [22]:
data['post_body'].sample(10)

4226213     minhyukslatina : jimin ’s   thighs are so thick , but you know what else is thick ? dats rite , his heart                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   

# Process data

## Concatenate posts

In [5]:
import pandas as pd
import csv
import os
from tqdm import tqdm_notebook as tqdm

community = 'bts'
data_dirpath = f'../../data/{community}_posts'

posts = []
for fname in tqdm(os.listdir(data_dirpath)):
    fpath = os.path.join(data_dirpath, fname)
    try:
        part = pd.read_csv(fpath, sep='\t')
    except:
        part = pd.read_csv(fpath, sep='\t', engine='python', quoting=csv.QUOTE_NONE, error_bad_lines=False, warn_bad_lines=False)
    posts.extend(part.values.tolist())

Skipping line 10553: Expected 25 fields in line 10553, saw 71
Skipping line 10554: Expected 25 fields in line 10554, saw 68
Skipping line 21583: Expected 25 fields in line 21583, saw 27
Skipping line 2119: Expected 25 fields in line 2119, saw 26
Skipping line 2121: Expected 25 fields in line 2121, saw 26
Skipping line 3161: Expected 25 fields in line 3161, saw 30
Skipping line 5221: Expected 25 fields in line 5221, saw 30
Skipping line 5222: Expected 25 fields in line 5222, saw 30
Skipping line 5223: Expected 25 fields in line 5223, saw 30
Skipping line 5227: Expected 25 fields in line 5227, saw 30
Skipping line 5234: Expected 25 fields in line 5234, saw 30
Skipping line 12004: Expected 25 fields in line 12004, saw 77
Skipping line 12005: Expected 25 fields in line 12005, saw 77
Skipping line 13164: Expected 25 fields in line 13164, saw 26
Skipping line 13289: Expected 25 fields in line 13289, saw 51
Skipping line 13290: Expected 25 fields in line 13290, saw 51
Skipping line 13291: Exp

Skipping line 10313: Expected 25 fields in line 10313, saw 61
Skipping line 14050: Expected 25 fields in line 14050, saw 92
Skipping line 18824: Expected 25 fields in line 18824, saw 29
Skipping line 2129: Expected 25 fields in line 2129, saw 26
Skipping line 6596: Expected 25 fields in line 6596, saw 91
Skipping line 6601: Expected 25 fields in line 6601, saw 91
Skipping line 5122: Expected 25 fields in line 5122, saw 164
Skipping line 5124: Expected 25 fields in line 5124, saw 164
Skipping line 5248: Expected 25 fields in line 5248, saw 43
Skipping line 5249: Expected 25 fields in line 5249, saw 43
Skipping line 13627: Expected 25 fields in line 13627, saw 158
Skipping line 13628: Expected 25 fields in line 13628, saw 158
Skipping line 2749: Expected 25 fields in line 2749, saw 64
Skipping line 3572: Expected 25 fields in line 3572, saw 29
Skipping line 20443: Expected 25 fields in line 20443, saw 29
Skipping line 14138: field larger than field limit (131072)
Skipping line 14139: fie

Skipping line 5210: Expected 25 fields in line 5210, saw 26
Skipping line 5211: Expected 25 fields in line 5211, saw 26
Skipping line 9891: Expected 25 fields in line 9891, saw 36
Skipping line 9892: Expected 25 fields in line 9892, saw 36
Skipping line 9937: Expected 25 fields in line 9937, saw 31
Skipping line 9938: Expected 25 fields in line 9938, saw 31
Skipping line 13057: Expected 25 fields in line 13057, saw 27
Skipping line 13058: Expected 25 fields in line 13058, saw 27
Skipping line 6168: Expected 25 fields in line 6168, saw 38
Skipping line 6169: Expected 25 fields in line 6169, saw 38
Skipping line 3785: Expected 25 fields in line 3785, saw 60
Skipping line 3789: Expected 25 fields in line 3789, saw 60
Skipping line 3792: Expected 25 fields in line 3792, saw 60
Skipping line 14798: Expected 25 fields in line 14798, saw 26
Skipping line 24271: Expected 25 fields in line 24271, saw 30
Skipping line 24276: Expected 25 fields in line 24276, saw 69
Skipping line 24319: Expected 

Skipping line 8595: Expected 25 fields in line 8595, saw 55
Skipping line 8596: Expected 25 fields in line 8596, saw 55
Skipping line 8597: Expected 25 fields in line 8597, saw 55
Skipping line 8607: Expected 25 fields in line 8607, saw 71
Skipping line 11988: Expected 25 fields in line 11988, saw 32
Skipping line 12702: Expected 25 fields in line 12702, saw 50
Skipping line 12733: Expected 25 fields in line 12733, saw 50
Skipping line 18683: Expected 25 fields in line 18683, saw 27
Skipping line 18693: Expected 25 fields in line 18693, saw 29
Skipping line 19513: Expected 25 fields in line 19513, saw 78
Skipping line 19520: Expected 25 fields in line 19520, saw 29
Skipping line 19524: Expected 25 fields in line 19524, saw 42
Skipping line 19526: Expected 25 fields in line 19526, saw 29
Skipping line 19664: Expected 25 fields in line 19664, saw 70
Skipping line 19667: Expected 25 fields in line 19667, saw 54
Skipping line 19669: Expected 25 fields in line 19669, saw 49
Skipping line 19

Skipping line 3031: field larger than field limit (131072)
Skipping line 3032: field larger than field limit (131072)
Skipping line 2011: Expected 25 fields in line 2011, saw 57
Skipping line 6773: Expected 25 fields in line 6773, saw 28
Skipping line 6774: Expected 25 fields in line 6774, saw 28
Skipping line 12211: Expected 25 fields in line 12211, saw 26
Skipping line 15691: Expected 25 fields in line 15691, saw 30
Skipping line 11199: Expected 25 fields in line 11199, saw 34
Skipping line 11202: Expected 25 fields in line 11202, saw 29
Skipping line 2993: Expected 25 fields in line 2993, saw 93
Skipping line 14751: Expected 25 fields in line 14751, saw 46
Skipping line 61: field larger than field limit (131072)
Skipping line 64: field larger than field limit (131072)
Skipping line 13535: Expected 25 fields in line 13535, saw 66
Skipping line 8515: Expected 25 fields in line 8515, saw 100
Skipping line 8516: Expected 25 fields in line 8516, saw 100
Skipping line 8549: Expected 25 fi

...

Skipping line 8952: Expected 25 fields in line 8952, saw 32
Skipping line 8953: Expected 25 fields in line 8953, saw 32
Skipping line 472: field larger than field limit (131072)
Skipping line 2091: Expected 25 fields in line 2091, saw 383
Skipping line 2092: Expected 25 fields in line 2092, saw 383
Skipping line 2189: Expected 25 fields in line 2189, saw 383
Skipping line 5708: Expected 25 fields in line 5708, saw 45
Skipping line 5709: Expected 25 fields in line 5709, saw 45
Skipping line 6018: Expected 25 fields in line 6018, saw 42
Skipping line 6028: Expected 25 fields in line 6028, saw 39
Skipping line 6029: Expected 25 fields in line 6029, saw 39
Skipping line 7176: Expected 25 fields in line 7176, saw 26
Skipping line 14501: Expected 25 fields in line 14501, saw 27
Skipping line 14502: Expected 25 fields in line 14502, saw 27
Skipping line 8128: Expected 25 fields in line 8128, saw 55
Skipping line 8129: Expected 25 fields in line 8129, saw 55
Skipping line 6400: Expected 25 fie

Skipping line 3463: field larger than field limit (131072)
Skipping line 3464: field larger than field limit (131072)
Skipping line 11840: Expected 25 fields in line 11840, saw 52
Skipping line 11853: Expected 25 fields in line 11853, saw 52
Skipping line 10392: Expected 25 fields in line 10392, saw 63
Skipping line 16983: Expected 25 fields in line 16983, saw 59
Skipping line 16984: Expected 25 fields in line 16984, saw 59
Skipping line 17359: Expected 25 fields in line 17359, saw 101
Skipping line 17361: Expected 25 fields in line 17361, saw 101
Skipping line 17365: Expected 25 fields in line 17365, saw 28
Skipping line 17366: Expected 25 fields in line 17366, saw 28
Skipping line 4552: Expected 25 fields in line 4552, saw 36
Skipping line 4559: Expected 25 fields in line 4559, saw 47
Skipping line 4567: Expected 25 fields in line 4567, saw 70
Skipping line 4583: Expected 25 fields in line 4583, saw 54
Skipping line 2930: Expected 25 fields in line 2930, saw 34
Skipping line 7137: Ex

Skipping line 6584: Expected 25 fields in line 6584, saw 30
Skipping line 6585: Expected 25 fields in line 6585, saw 30
Skipping line 10815: Expected 25 fields in line 10815, saw 27
Skipping line 10970: Expected 25 fields in line 10970, saw 27
Skipping line 1988: Expected 25 fields in line 1988, saw 41
Skipping line 2260: Expected 25 fields in line 2260, saw 77
Skipping line 9369: Expected 25 fields in line 9369, saw 110
Skipping line 9370: Expected 25 fields in line 9370, saw 110
Skipping line 9371: Expected 25 fields in line 9371, saw 110
Skipping line 13424: Expected 25 fields in line 13424, saw 50
Skipping line 14041: Expected 25 fields in line 14041, saw 74
Skipping line 8736: Expected 25 fields in line 8736, saw 37
Skipping line 8737: Expected 25 fields in line 8737, saw 37
Skipping line 8778: Expected 25 fields in line 8778, saw 37
Skipping line 8779: Expected 25 fields in line 8779, saw 37
Skipping line 8807: Expected 25 fields in line 8807, saw 43
Skipping line 8808: Expected 

Skipping line 1107: Expected 25 fields in line 1107, saw 26
Skipping line 7445: field larger than field limit (131072)
Skipping line 7446: field larger than field limit (131072)
Skipping line 7447: field larger than field limit (131072)
Skipping line 4440: Expected 25 fields in line 4440, saw 26
Skipping line 4824: Expected 25 fields in line 4824, saw 26
Skipping line 9722: Expected 25 fields in line 9722, saw 40
Skipping line 10653: Expected 25 fields in line 10653, saw 33
Skipping line 13136: Expected 25 fields in line 13136, saw 35
Skipping line 13412: Expected 25 fields in line 13412, saw 35
Skipping line 13776: Expected 25 fields in line 13776, saw 53
Skipping line 6121: field larger than field limit (131072)
Skipping line 2473: Expected 25 fields in line 2473, saw 60
Skipping line 5194: Expected 25 fields in line 5194, saw 33
Skipping line 5205: Expected 25 fields in line 5205, saw 48
Skipping line 5209: Expected 25 fields in line 5209, saw 36
Skipping line 5215: Expected 25 fiel

Skipping line 3536: Expected 25 fields in line 3536, saw 50
Skipping line 3539: Expected 25 fields in line 3539, saw 50
Skipping line 11197: Expected 25 fields in line 11197, saw 58
Skipping line 12181: Expected 25 fields in line 12181, saw 29
Skipping line 12272: Expected 25 fields in line 12272, saw 163
Skipping line 12273: Expected 25 fields in line 12273, saw 163
Skipping line 15306: Expected 25 fields in line 15306, saw 120
Skipping line 15307: Expected 25 fields in line 15307, saw 120
Skipping line 3512: Expected 25 fields in line 3512, saw 87
Skipping line 4164: Expected 25 fields in line 4164, saw 32
Skipping line 4165: Expected 25 fields in line 4165, saw 32
Skipping line 15902: Expected 25 fields in line 15902, saw 30
Skipping line 7711: Expected 25 fields in line 7711, saw 53
Skipping line 7712: Expected 25 fields in line 7712, saw 53
Skipping line 8703: Expected 25 fields in line 8703, saw 52
Skipping line 10295: Expected 25 fields in line 10295, saw 39
Skipping line 10296:

In [6]:
data = pd.DataFrame(posts, columns=part.columns)
print(data.columns)
print(data.shape)

Index(['post_tags_string', 'post_id', 'activity_time_epoch', 'tumblelog_id',
       'is_private', 'post_title', 'post_short_url', 'post_slug', 'post_type',
       'post_caption', 'post_format', 'post_note_count', 'post_tags',
       'post_content', 'reblogged_from_post_id', 'reblogged_from_metadata',
       'created_time_epoch', 'updated_time_epoch', 'is_submission', 'mentions',
       'source_title', 'source_url', 'post_classifier', 'blog_classifier',
       'activity_date'],
      dtype='object')
(23580747, 25)


## Remove duplicate posts, non-string posts

In [7]:
data.drop_duplicates('post_id', inplace=True)
data.shape

(1692294, 25)

In [8]:
data.dropna(subset=['post_id'], inplace=True)
data.shape

(1692293, 25)

In [9]:
data = data[data['post_content'].map(lambda x: isinstance(x, str) and len(x) > 0)]
data.shape

(1352536, 25)

## Preprocess text

In [10]:
import re
import spacy

from html.parser import HTMLParser

class MLStripper(HTMLParser):
    def __init__(self):
        super().__init__()
        self.reset()
        self.fed = []
    def handle_data(self, d):
        self.fed.append(d)
    def get_data(self):
        return ' '.join(self.fed)

def strip_tags(html):
    s = MLStripper()
    s.feed(html)
    return s.get_data()

nlp = spacy.load('en', disable=['tagger', 'parser', 'ner'])

def process_text(text):
    """ Extract body of text, preprocess it """
    
    if not isinstance(text, str):
        return ''
    
    m = re.search(r'body=(.*), note_count', text)
    if not m: return ''
    body = m.group(1)
    
    # Strip HTML 
    body = strip_tags(body)
    
    # Tokenize
    toks = [tok.text for tok in nlp.tokenizer(body.lower())]
    
    return ' '.join(toks)

In [11]:
data['post_body'] = list(map(process_text, tqdm(data['post_content'])))

In [12]:
data = data[data['post_body'].map(lambda x: len(x) > 0)]
data.shape

(575920, 26)

## Save out

In [14]:
data.to_csv(f'../../data/{community}_posts.csv', index=False)

# Extract stylistic features

In [15]:
from string import punctuation
from nltk.corpus import words

en_words = set(words.words())
def extract_style_features(text):
    
    features = {}
    
    # Number of words
    toks = text.split()
    n_words = len(toks)
    features['n_words'] = n_words
    features['n_characters'] = len(text)
    
    if n_words == 0: return features
   
    # Number, which punctuation
    total_punctuation = 0
    for p in punctuation:
        p_count = text.count(p)
        features[p] = p_count
        total_punctuation += p_count
    features['avg_punctuation'] = total_punctuation/n_words
    
    # Capitalization
    total_capitals = sum(1 for c in text if c.isupper())
    word_initial_capitals = sum(1 for w in toks if w[0].isupper())
    features['n_capitals'] = total_capitals
    features['avg_capitalized_words'] = word_initial_capitals/n_words
    features['avg_capitalized_letters'] = total_capitals/features['n_characters']
    
    # Out-of-vocabulary words
    features['n_oov'] = sum(1 for w in toks if not w in en_words)
    features['avg_oov'] = features['n_oov']/features['n_words']
    
    # Repeated characters
    total_char_repeats = 0
    for char in set(text):
        repeated_count = text.count(''.join([char]*3))
        if repeated_count > 0:
            features[f'repeated_{char}'] = repeated_count
            total_char_repeats += repeated_count
            
    features['total_char_repeats'] = total_char_repeats
    
    return features

In [17]:
pd.set_option('display.max_colwidth', -1)

In [20]:
test = data.loc[1, 'post_content']
test

'{mentions={}, format=html, title=, body=<p>Lance: you just have to be the bigger person and let it go.</p><p>Allura: Okay. *uses her shape shifting power to grow taller* I don?t see how this is supposed to make me want to let it go.</p>, note_count=0, slug=lance-you-just-have-to-be-the-bigger-person-and, tags={(voltron),(allurance),(lallura)}}'

In [16]:
data['style_features'] = list(map(extract_style_features, tqdm(data['post_body'])))

In [18]:
data.to_pickle(f'../../data/{community}_posts.pkl')